In [57]:
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path
from pyaxis import pyaxis
import matplotlib.font_manager as fm 
from matplotlib.lines import Line2D
from matplotlib.patches import Patch

In [58]:
# Load the "Jost" font needed for this plot
font_dir = ['./Jost_Font/']  # Font is located in Jost_Font folder
for font in fm.findSystemFonts(font_dir):
    fm.fontManager.addfont(font)

In [59]:
gpd.options.io_engine = "pyogrio"

In [60]:
data = pd.read_csv("./NRW2023-wahlbeteiligung.csv", sep=';')

In [61]:
avg_participation = data["wahlbeteiligung"][0]

In [62]:
data_municipality = data[data["ebene_resultat"].isin(["Gemeinde"])]

In [63]:
border_layout_folder = Path("./boundaries")
municipality_border = border_layout_folder / "k4g23.shx"
canton_border = border_layout_folder / "k4k23.shx"

In [64]:
map_canton = gpd.read_file(str(canton_border))
map_municipality = gpd.read_file(str(municipality_border))

In [65]:
data_municipality = data_municipality.rename(columns={'gemeinde_bezeichnung': 'GMDNAME'})
map_municipality = map_municipality.merge(data_municipality, on="GMDNAME")

In [80]:
sorted_by_participation = map_municipality.sort_values('wahlbeteiligung')

In [68]:
from matplotlib.colors import LinearSegmentedColormap

cmap = LinearSegmentedColormap.from_list(name="my_cmap", 
                                                colors=["darkred", "indianred", "white", "limegreen", "darkgreen"], N=6)

In [83]:
legend_elements_negative = [
       Patch(facecolor='#900303', label='> 16%'),
       Patch(facecolor='#c44a4a', label='8—16%'),
       Patch(facecolor='#eebdbd', label='0—8%'),
]

legend_elements_positive = [
       Patch(facecolor='#006311', label='> 16%'),
       Patch(facecolor='#02b639', label='8—16%'),
       Patch(facecolor='#a8eaaf', label='0—8%'),
]

legend_kwargs = {
       'prop': {'family': 'Jost', 'size': 18, 'weight': 'regular'}, 
       'labelcolor': 'dimgrey', 
       'framealpha': 0, 
       'labelspacing': 0.1, 
       'handlelength': 1.5, 
       'handleheight': 1, 
       'handletextpad': 0.4,
}

arrowprops = {
       'arrowstyle': 'simple',
       'color': 'black',
}

annotation_items = {
    'highest': [sorted_by_participation.tail(1), (0.5, 0.1)],
    'lowest': [sorted_by_participation.head(1), (0.9, 0.9)],
}


In [75]:
def do_annotations(axis):
    for key, item in annotation_items.items():
        axis.annotate(
            key,
            xy=(item[0]['geometry'].centroid.x, item[0]['geometry'].centroid.y), xycoords='data',
            xytext=item[1], textcoords='axes fraction',
            size=30, va="center", ha="center",
            arrowprops={'connectionstyle': "arc3,rad=-0.2", **arrowprops},
            fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'}
        )

In [84]:
# Create figure and axis
f, ax = plt.subplots(figsize=(36, 27), dpi=300)
p = map_municipality.plot(column="wahlbeteiligung", ax=ax, linewidth=1, edgecolor='white', cmap=cmap, vmin=avg_participation - 24, vmax= avg_participation + 24)
map_canton.plot(ax=ax, linewidth=3.5, edgecolor='black', color=(0, 0, 0, 0))

ax.tick_params(which='both', bottom=False, top=False, right=False, left=False, labelleft=False, labelbottom=False) 

ax.spines.bottom.set_visible(False)
ax.spines.top.set_visible(False)
ax.spines.left.set_visible(False)
ax.spines.right.set_visible(False)

do_annotations(ax)

f.legend(handles=legend_elements_negative, bbox_to_anchor=(0.3205, 0.85), **legend_kwargs)
f.legend(handles=legend_elements_positive, bbox_to_anchor=(0.2605, 0.85), **legend_kwargs)

# Set title
f.suptitle('Voter Participation on Municipality Level', fontproperties={'family': 'Jost', 'size': 60, 'weight': 'bold'}, x=0.37, y=0.9)

# Set subtitle (there might be a better way, but I could not find a way to have differently colored text in one object...)
f.text(x=0.157, y=0.85, s=f"Difference —              and               — in voter participation, compared to the", 
       color='dimgrey', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'regular'})
f.text(x=0.2181, y=0.85, s="positive", color='#006311', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
f.text(x=0.2782, y=0.85, s="negative", color='#900303', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})
f.text(x=0.508, y=0.85, s=f"Swiss average of {avg_participation:.1f}%", color='black', fontproperties={'family': 'Jost', 'size': 27, 'weight': 'semibold'})

# Save the figure -> the output "plot.png" looks a lot closer to the original than the one displayed in this notebook
plt.savefig('voter_participation_community.png', bbox_inches='tight', pad_inches=0.5)

c:\git\data-visualizations\.env3\lib\site-packages\matplotlib\text.py:1461: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  x = float(self.convert_xunits(x))
c:\git\data-visualizations\.env3\lib\site-packages\matplotlib\text.py:1463: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  y = float(self.convert_yunits(y))
